## Лабораторная 6

#### Задание:
- Развернуть и запустить проект по реализации обучения с подкреплением для игры "Крестики-нолики".
- Перевести проект на библиотеку gymnasium и современную версию Python. 
- Реализовать агента для игры "Крестики-нолики" в виде отдельного класса (по примеру из лекции). 
- Переписать основной цикл обучения для работы с отдельным классом агента (по примеру из лекции). Выполнить тестирование новой версии программы.

Исходный проект: https://github.com/nczempin/gym-tic-tac-toe

#### Перевод проекта на Gymnasium

Gymnasium — библиотека Python для разработки, обучения и тестирования моделей обучения с подкреплением (Reinforcement Learning). Это обновлённая версия OpenAI Gym с улучшенной функциональностью и совместимостью.

Основные компоненты Gymnasium:

1. Action Space (пространство действий):
   - Определяет возможные действия, которые агент может предпринимать. Например:
     - spaces.Discrete(9) — дискретные действия от 0 до 8 (например, выбор клетки на игровом поле).

2. Observation Space (пространство наблюдений):
   - Определяет, какие данные агент получает о текущем состоянии среды.
     - Например, состояние игрового поля: spaces.Discrete(9 * 3 * 2).

3. Методы среды:
   - reset(): Сбрасывает среду и возвращает её начальное состояние.
   - step(action): Выполняет действие агента и возвращает следующую информацию:
     - Новое состояние среды.
     - Награду за действие.
     - Флаг завершения (True/False).
     - Дополнительные данные.
   - render(): Отображает состояние среды (например, визуализация игрового поля).
   - close(): Закрывает среду.

In [13]:
import gymnasium as gym
from gymnasium import spaces
import random

class TicTacToeEnv(gym.Env):
    metadata = {'render.modes': ['human']}
    
    symbols = ['O', ' ', 'X']

    def __init__(self):
        super().__init__()
        self.action_space = spaces.Discrete(9)
        self.observation_space = spaces.Discrete(9 * 3 * 2) 
        self.reset()

    def step(self, action):
        done = False
        reward = 0

        p, square = action

        board = self.state['board']
        proposed = board[square] 
        om = self.state['on_move'] 
        if proposed != 0:
            print(f"Незаконный ход: Квадрат {square} уже занят.")
            done = True
            reward = -1 * om 
        if p != om: 
            print(f"Незаконный ход: игрок {p} не находится в движении")
            done = True
            reward = -1 * om
        else:
            board[square] = p
            self.state['on_move'] = -p

        for i in range(3):
            if (board[i * 3] == p and board[i * 3 + 1] == p and board[i * 3 + 2] == p) or \
               (board[i] == p and board[i + 3] == p and board[i + 6] == p):
                reward = p
                done = True
                break

        if (board[0] == p and board[4] == p and board[8] == p) or \
           (board[2] == p and board[4] == p and board[6] == p):
            reward = p
            done = True
                
        return self.state, reward, done, {}

    def reset(self):
        self.state = {}
        self.state['board'] = [0, 0, 0, 0, 0, 0, 0, 0, 0] 
        self.state['on_move'] = 1 
        return self.state, {}

    def render(self, close=False):
        if close:
            return
        print("шаг: " , self.symbols[self.state['on_move']+1])
        for i in range (9):
            print (self.symbols[self.state['board'][i]+1], end=" ")
            if ((i % 3) == 2):
                print()

    def move_generator(self):
        moves = []
        for i in range(9):
            if self.state['board'][i] == 0:
                p = self.state['on_move']
                m = [p, i]
                moves.append(m)
        return moves

#### Агент
1. Взаимодействие со средой:
   - Агент передаёт свои действия через метод step(action), где:
     - action — кортеж (p, square), где:
       - p: текущий игрок (1 для "X", -1 для "O").
       - square: номер клетки (0–8).
   - Среда проверяет, допустимо ли действие, обновляет состояние игры, вычисляет награду и определяет, завершилась ли игра.

2. Решение задач агента:
   - Агент должен:
     - Выбирать клетку на игровом поле, соблюдая правила.
     - Стремиться к победе, формируя вертикальные, горизонтальные или диагональные линии из своих символов.
     - Избегать неправильных действий, которые приводят к штрафам (например, выбор занятой клетки).

3. Система наград:
   - Агент получает:
     - Положительную награду за победу (соответствует значению игрока p).
     - Отрицательную награду за ошибочные действия (например, попытка занять уже занятую клетку).
     - Нулевую награду за допустимые, но не победные ходы.

In [14]:
class Agent:
    def __init__(self, symbol):
        self.symbol = symbol
    
    def get_action(self, moves):
        return random.choice(moves)

#### Цикл обучения

In [15]:
environment = TicTacToeEnv()

agent = Agent(symbol=1)

num_episodes = 100 
collected_rewards = [] 

oom = 1

for i in range(num_episodes):
    state, _ = environment.reset() 

    total_reward = 0

    done = False
    om = oom 

    for j in range(9): 
        moves = environment.move_generator() 

        if not moves:
            break

        
        if len(moves) == 1:
            move = moves[0]
        else:
            move = agent.get_action(moves)

        next_state, reward, done, info = environment.step(move)
        total_reward += reward
        state = next_state

        environment.render()

        if done:
            break

        om = -om

    collected_rewards.append(total_reward)

    print(f"Эпизод {i+1}, Общая награда: {total_reward}")
    average_reward = sum(collected_rewards) / len(collected_rewards)
    print(f"Средняя награда: {average_reward}")

шаг:  O
      
      
X     
шаг:  X
      
      
X O   
шаг:  O
  X   
      
X O   
шаг:  X
  X   
O     
X O   
шаг:  O
  X X 
O     
X O   
шаг:  X
  X X 
O     
X O O 
шаг:  O
  X X 
O X   
X O O 
Эпизод 1, Общая награда: 1
Средняя награда: 1.0
шаг:  O
      
      
    X 
шаг:  X
O     
      
    X 
шаг:  O
O     
  X   
    X 
шаг:  X
O O   
  X   
    X 
шаг:  O
O O   
  X   
X   X 
шаг:  X
O O   
O X   
X   X 
шаг:  O
O O   
O X X 
X   X 
шаг:  X
O O O 
O X X 
X   X 
Эпизод 2, Общая награда: -1
Средняя награда: 0.0
шаг:  O
      
X     
      
шаг:  X
O     
X     
      
шаг:  O
O     
X X   
      
шаг:  X
O     
X X O 
      
шаг:  O
O     
X X O 
    X 
шаг:  X
O   O 
X X O 
    X 
шаг:  O
O   O 
X X O 
  X X 
шаг:  X
O   O 
X X O 
O X X 
шаг:  O
O X O 
X X O 
O X X 
Эпизод 3, Общая награда: 1
Средняя награда: 0.3333333333333333
шаг:  O
X     
      
      
шаг:  X
X     
O     
      
шаг:  O
X   X 
O     
      
шаг:  X
X   X 
O     
O     
шаг:  O
X   X 
O     
O X   